In [1]:
# import library
import requests
import re
from bs4 import BeautifulSoup
import pandas as pd
import numpy as np
from datetime import datetime
import os
import plotly.express as px
import geopandas as gpd
import folium
from tqdm.notebook import tqdm
from folium import Marker
from folium.plugins import MarkerCluster

In [3]:
# get the current working directory
cwd = os.getcwd()

# print the current working directory
print(f"Current working directory: {cwd}")

path = '/Users/johnn/Documents/Research/codebook/covid/'
os.chdir(path)

# get the current working directory
cwd = os.getcwd()
# print the current working directory
print(f"Current working directory: {cwd}")


Current working directory: c:\Users\johnn\Documents\Research\codebook\covid
Current working directory: c:\Users\johnn\Documents\Research\codebook\covid


In [4]:
# define global parameters for web scrapping.
headers = {'user-agent':'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/99.0.4844.84 Safari/537.36'}

In [5]:
# draw map
def embed_map(m, file_name):
    from IPython.display import IFrame
    m.save(file_name)
    return IFrame(file_name, width='100%', height='500px')

In [6]:
# request address
def transformer(geo):
    parameters = {'address': geo, 'key': '38f20eb40106630346281a14392f3629', 'city':'shanghai', 'batch':'true'}
    base = 'https://restapi.amap.com/v3/geocode/geo'
    try:
        response = requests.get(base, parameters, timeout=30)
        answer = response.json()
        return answer
    except:
        return None

In [27]:
# load link table
result_sorted = pd.read_csv('link_all.csv')
result_sorted.drop(columns='Unnamed: 0', inplace=True)

In [36]:
date = datetime.strptime('2022-04-10', '%Y-%m-%d')
link = 'https://mp.weixin.qq.com/s/u0XfHF8dgfEp8vGjRtcwXA'
#date = pd.to_datetime('2022-04-09', format='%Y-%m-%d')

In [37]:
result_sorted = pd.concat([result_sorted, pd.DataFrame({"date": [date], "link": [link]})], ignore_index=True)

In [38]:
len(result_sorted)

23

In [39]:
result_sorted['date'] = pd.to_datetime(result_sorted['date'])

In [40]:
result_sorted.to_csv('link_all.csv')

In [74]:
# parse address from the webpage
def parse_address(date):
    regex_str = '[\u4E00-\u9FA5]*[0-9]*[\u4E00-\u9FA5]*[0-9]*[\u4E00-\u9FA5]*(?=[\uff0c|\u3002|\u3001|\uff08|\s])?'
    r = requests.get(result_sorted[result_sorted['date']==date]['link'].values[0], headers=headers)
    r.encoding = 'utf-8'
    soup = BeautifulSoup(r.text, 'lxml')
    address = []
    cleaned_address = pd.DataFrame()
    #for x in soup1.find('div', {'id':'ivs_content', 'class':'Article_content'}).find_all('p'):
    for x in soup.find_all('p'):
        if re.match(regex_str, x.text) and "已对相关居住地落实终末消毒措施" not in x.text:
            address.append(re.match(regex_str, x.text).group(0))
    cleaned_address['address'] = address
    cleaned_address['date'] = date
    #cleaned_address['address'] = '上海市' + cleaned_address['address']
    return cleaned_address

# parse the address from refined address
def parse_json_address(date):
    result = pd.DataFrame()
    result['country'] = [x['geocodes'][0]['country'] if len(x['geocodes'][0]['district']) != 0 else 'None' for x in real_address]
    result['province'] = [x['geocodes'][0]['province'] if len(x['geocodes'][0]['district']) != 0 else 'None' for x in real_address]
    result['citycode'] = [x['geocodes'][0]['citycode'] if len(x['geocodes'][0]['district']) != 0 else 'None' for x in real_address]
    result['city'] = [x['geocodes'][0]['city'] if len(x['geocodes'][0]['district']) != 0 else 'None' for x in real_address]
    result['district'] = [x['geocodes'][0]['district'] if len(x['geocodes'][0]['district']) != 0 else 'None' for x in real_address]
    result['location'] = [x['geocodes'][0]['location'] if len(x['geocodes'][0]['district']) != 0 else 'None' for x in real_address]
    result['long'] = result['location'].str.split(',', expand=True)[0]
    result['lat'] = result['location'].str.split(',', expand=True)[1]
    result['date'] = date
    assert cleaned_address['date'][0] == date, 'wrong date'
    result['address'] = cleaned_address[cleaned_address['date'] == date]['address']
    result.drop(result[result['country']=='None'].index, inplace=True)
    return result

In [75]:
tqdm.pandas()
cleaned_address = parse_address(date)
cleaned_address

address       date
0                 2022-04-10
1                 2022-04-10
2                 2022-04-10
3          市卫健委今早 2022-04-10
4                 2022-04-10
...           ...        ...
6386              2022-04-10
6387              2022-04-10
6388           资料 2022-04-10
6389           编辑 2022-04-10
6390  微信扫一扫关注该公众号 2022-04-10

[6391 rows x 2 columns]

In [95]:
# 分地区
index_start = []
index_start.append(cleaned_address[cleaned_address['address'] == '安基村朱家宅'].index.values[0])
index_start.append(cleaned_address[cleaned_address['address'] == '百翎路5号'].index.values[0])
index_start.append(cleaned_address[cleaned_address['address'] == '安远路139号'].index.values[0])
index_start.append(cleaned_address[cleaned_address['address'] == '安福路183号'].index.values[0])
index_start.append(cleaned_address[cleaned_address['address'] == '安龙路929弄'].index.values[0])
index_start.append(cleaned_address[cleaned_address['address'] == '安远路188弄'].index.values[0])
index_start.append(cleaned_address[cleaned_address['address'] == '安汾路780弄'].index.values[0])
index_start.append(cleaned_address[cleaned_address['address'] == '爱国二村'].index.values[0])
index_start.append(cleaned_address[cleaned_address['address'] == '爱辉路213号'].index.values[0])
index_start.append(cleaned_address[cleaned_address['address'] == '爱国村'].index.values[0])
index_start.append(cleaned_address[cleaned_address['address'] == '阿克苏路66弄'].index.values[0])
index_start.append(cleaned_address[cleaned_address['address'] == '东新村'].index.values[0])
index_start.append(cleaned_address[cleaned_address['address'] == '伴亭路500号'].index.values[0])
index_start.append(cleaned_address[cleaned_address['address'] == '爱星村'].index.values[0])
index_start.append(cleaned_address[cleaned_address['address'] == '安邬路188号'].index.values[0])
index_start.append(cleaned_address[cleaned_address['address'] == '江南大道'].index.values[0])

In [93]:
# 分地区
index_end = []
index_end.append(cleaned_address[cleaned_address['address'] == '邹平路191号工地生活区'].index.values[0])
index_end.append(cleaned_address[cleaned_address['address'] == '自忠路373号'].index.values[0])
index_end.append(cleaned_address[cleaned_address['address'] == '中兴路461弄'].index.values[0])
index_end.append(cleaned_address[cleaned_address['address'] == '中山西路2366弄'].index.values[0])
index_end.append(cleaned_address[cleaned_address['address'] == '遵义路820号'].index.values[0])
index_end.append(cleaned_address[cleaned_address['address'] == '棕榈路451弄'].index.values[0])
index_end.append(cleaned_address[cleaned_address['address'] == '株洲路9弄'].index.values[0])
index_end.append(cleaned_address[cleaned_address['address'] == '周家嘴路4214弄'].index.values[0])
index_end.append(cleaned_address[cleaned_address['address'] == '朱家弄村'].index.values[0])
index_end.append(cleaned_address[cleaned_address['address'] == '紫藤一村'].index.values[0])
index_end.append(cleaned_address[cleaned_address['address'] == '竹笛路388弄'].index.values[0])
index_end.append(cleaned_address[cleaned_address['address'] == '亿横建材市场'].index.values[0])
index_end.append(cleaned_address[cleaned_address['address'] == '庄家村'].index.values[0])
index_end.append(cleaned_address[cleaned_address['address'] == '诸陆西路1737弄'].index.values[0])
index_end.append(cleaned_address[cleaned_address['address'] == '资福村'].index.values[0])
index_end.append(cleaned_address[cleaned_address['address'] == '建筑工地'].index.values[0])

In [90]:
district = ['浦东新区', '黄浦区', '静安区', '徐汇区', 
            '长宁区', '普陀区', '虹口区', '杨浦区', '宝山区', 
            '闵行区', '嘉定区', '金山区', '松江区', '青浦区',
            '奉贤区', '崇明区']

In [103]:
cleaned_address_new = pd.DataFrame()
for i in range(len(index_start)):
    cleaned_address_new = pd.concat(cleaned_address_new, cleaned_address.loc[index_start[i]:(index_end[i]+1)], ignore_index=True)

C:\Users\johnn\AppData\Local\Temp\ipykernel_11044\4257457929.py:3: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only
  cleaned_address_new = pd.concat(cleaned_address_new, cleaned_address.loc[index_start[i]:(index_end[i]+1)], ignore_index=True)


TypeError: first argument must be an iterable of pandas objects, you passed an object of type "DataFrame"

In [102]:
cleaned_address_new.loc[0]

KeyError: 0

In [173]:
real_address = cleaned_address['address'].progress_apply(lambda x: transformer(x))

  0%|          | 0/4770 [00:00<?, ?it/s]

In [174]:
result = parse_json_address(date)

In [175]:
result

country province citycode city district              location  \
0         中国      上海市      021  上海市     浦东新区  121.568585,31.342882   
1         中国      上海市      021  上海市     浦东新区  121.548341,31.166473   
2         中国      上海市      021  上海市      奉贤区  121.540789,30.951220   
3         中国      上海市      021  上海市     浦东新区  121.576675,31.234985   
4         中国      上海市      021  上海市     浦东新区  121.555605,31.208224   
...      ...      ...      ...  ...      ...                   ...   
4765      中国      上海市      021  上海市      奉贤区  121.569825,30.931148   
4766      中国      上海市      021  上海市      奉贤区  121.482965,30.926979   
4767      中国      上海市      021  上海市      奉贤区  121.603450,30.966658   
4768      中国      上海市      021  上海市      崇明区  121.785770,31.328931   
4769      中国      上海市      021  上海市      崇明区  121.737243,31.373798   

            long        lat        date     address  
0     121.568585  31.342882  2022-04-09   上海市八灶村顾家宅  
1     121.548341  31.166473  2022-04-09   上海市八灶村张家宅  
2     121.540789  30.951220  2022-04-09   上海市八灶村赵家宅  
3     121.576675  31.234985  2022-04-09  上海市白桦路266弄  
4     121.555605  31.208224  2022-04-09  上海市白杨路199弄  
...          ...        ...         ...         ...  
4765  121.569825  30.931148  2022-04-09      上海市岳和村  
4766  121.482965  30.926979  2022-04-09  上海市展园路303弄  
4767  121.603450  30.966658  2022-04-09      上海市资福村  
4768  121.785770  31.328931  2022-04-09     上海市江南大道  
4769  121.737243  31.373798  2022-04-09  上海市长凯路253号  

[4755 rows x 10 columns]

In [84]:
result.drop_duplicates(subset='address', keep='first', inplace=True)

In [176]:
result.loc[result.address.duplicated(keep=False)]

country province citycode city district              location  \
25        中国      上海市      021  上海市      嘉定区  121.258821,31.466924   
395       中国      上海市      021  上海市      金山区  121.362088,30.870965   
1232      中国      上海市      021  上海市      宝山区  121.392493,31.414708   
1458      中国      上海市      021  上海市      松江区  121.314327,30.954207   
1560      中国      上海市      021  上海市      崇明区  121.688695,31.389857   
1630      中国      上海市      021  上海市      宝山区  121.316116,31.483445   
1659      中国      上海市      021  上海市     浦东新区  121.562722,31.126242   
3797      中国      上海市      021  上海市      宝山区  121.323400,31.405878   
3798      中国      上海市      021  上海市      宝山区  121.397812,31.305435   
3809      中国      上海市      021  上海市      闵行区  121.371019,31.103133   
3819      中国      上海市      021  上海市      宝山区  121.392493,31.414708   
3847      中国      上海市      021  上海市      闵行区  121.442667,31.055206   
3865      中国      上海市      021  上海市      宝山区  121.316116,31.483445   
3884      中国      上海市      021  上海市      闵行区  121.527956,31.006006   
3950      中国      上海市      021  上海市      金山区  121.362088,30.870965   
4042      中国      上海市      021  上海市      宝山区  121.347241,31.416784   
4073      中国      上海市      021  上海市      宝山区  121.323400,31.405878   
4168      中国      上海市      021  上海市      闵行区  121.442667,31.055206   
4183      中国      上海市      021  上海市      崇明区  121.688695,31.389857   
4234      中国      上海市      021  上海市      闵行区  121.527956,31.006006   
4317      中国      上海市      021  上海市      宝山区  121.397812,31.305435   
4351      中国      上海市      021  上海市      宝山区  121.398879,31.454291   
4507      中国      上海市      021  上海市      松江区  121.314327,30.954207   
4556      中国      上海市      021  上海市      嘉定区  121.258821,31.466924   
4681      中国      上海市      021  上海市      闵行区  121.442667,31.055206   
4697      中国      上海市      021  上海市      宝山区  121.398879,31.454291   
4710      中国      上海市      021  上海市     浦东新区  121.562722,31.126242   
4755      中国      上海市      021  上海市      宝山区  121.347241,31.416784   
4758      中国      上海市      021  上海市      闵行区  121.371019,31.103133   

            long        lat        date address  
25    121.258821  31.466924  2022-04-09  上海市北新村  
395   121.362088  30.870965  2022-04-09  上海市共和村  
1232  121.392493  31.414708  2022-04-09  上海市勤丰村  
1458  121.314327  30.954207  2022-04-09  上海市团结村  
1560  121.688695  31.389857  2022-04-09  上海市先进村  
1630  121.316116  31.483445  2022-04-09  上海市新苗村  
1659  121.562722  31.126242  2022-04-09  上海市秀龙村  
3797  121.323400  31.405878  2022-04-09  上海市联合村  
3798  121.397812  31.305435  2022-04-09  上海市联西村  
3809  121.371019  31.103133  2022-04-09  上海市梅园村  
3819  121.392493  31.414708  2022-04-09  上海市勤丰村  
3847  121.442667  31.055206  2022-04-09  上海市塘湾村  
3865  121.316116  31.483445  2022-04-09  上海市新苗村  
3884  121.527956  31.006006  2022-04-09  上海市正义村  
3950  121.362088  30.870965  2022-04-09  上海市共和村  
4042  121.347241  31.416784  2022-04-09  上海市金星村  
4073  121.323400  31.405878  2022-04-09  上海市联合村  
4168  121.442667  31.055206  2022-04-09  上海市塘湾村  
4183  121.688695  31.389857  2022-04-09  上海市先进村  
4234  121.527956  31.006006  2022-04-09  上海市正义村  
4317  121.397812  31.305435  2022-04-09  上海市联西村  
4351  121.398879  31.454291  2022-04-09  上海市新丰村  
4507  121.314327  30.954207  2022-04-09  上海市团结村  
4556  121.258821  31.466924  2022-04-09  上海市北新村  
4681  121.442667  31.055206  2022-04-09  上海市塘湾村  
4697  121.398879  31.454291  2022-04-09  上海市新丰村  
4710  121.562722  31.126242  2022-04-09  上海市秀龙村  
4755  121.347241  31.416784  2022-04-09  上海市金星村  
4758  121.371019  31.103133  2022-04-09  上海市梅园村

In [182]:
result.to_csv('report_4_09_filtered.csv')

In [91]:
result = pd.read_csv('report_4_09_filtered.csv')

In [183]:
m_1 = folium.Map(location=[31.230416, 121.473701], tiles='http://webrd02.is.autonavi.com/appmaptile?lang=zh_cn&size=1&scale=1&style=7&x={x}&y={y}&z={z}', titles='shanghaimap', attr='default', zoom_start=10)
home_lat = 31.180205
home_long = 121.507044
mc = MarkerCluster()
for idx, row in result.iterrows():
    mc.add_child(Marker(location=[row['lat'], row['long']], popup=f"地址：{row['address']},\n 日期：{row['date']}"))
# add home
Marker(location=[home_lat, home_long], popup='都市庭院（家）', icon=folium.Icon(color='red')).add_to(m_1)
m_1.add_child(mc)

In [184]:
embed_map(m_1, "4_9_map.html")

In [8]:
df_4_05 = pd.read_csv('report_4_05_filtered.csv')

In [9]:
df_4_06 = pd.read_csv('report_4_06_filtered.csv')

In [10]:
pd.merge(df_4_05.address, df_4_06.address, on='address', how='inner')

address
0     上海市板泉路1201弄
1     上海市板泉路2000弄
2     上海市板泉路2101弄
3     上海市北艾路1765弄
4      上海市北蔡大街31弄
...           ...
1793   上海市长橘路500弄
1794       上海市新港村
1795   上海市长凯路277号
1796       上海市创建村
1797       上海市向化村

[1798 rows x 1 columns]

In [24]:
df_4_06.loc[14,'address'] = '上海市浦东新区北新村'


In [25]:
df_4_06.loc[14]

Unnamed: 0                      17
country                         中国
province                       上海市
citycode                        21
city                           上海市
district                       嘉定区
location      121.258821,31.466924
long                    121.258821
lat                      31.466924
date                    2022-04-06
address                 上海市浦东新区北新村
Name: 14, dtype: object

In [20]:
test1[test1.duplicated(keep=False)]

14           上海市北新村
117          上海市城南村
172          上海市立新村
310          上海市顾家村
464          上海市团结村
478          上海市建新村
526          上海市金星村
565          上海市营房村
566          上海市沔青村
726          上海市沔青村
1061         上海市太平村
1099         上海市团结村
1238         上海市新苗村
1253         上海市星光村
1256         上海市幸福村
1258         上海市秀龙村
1349         上海市营房村
1402         上海市跃进村
3707         上海市新苗村
3740         上海市东街村
3751         上海市联合村
3963    上海市都会路3199弄
3964    上海市都会路3199弄
4050         上海市金星村
4079         上海市联合村
4182         上海市塘湾村
4194         上海市先进村
4201         上海市星火村
4233         上海市跃进村
4272         上海市北新村
4359         上海市东街村
4400         上海市顾家村
4428         上海市红光村
4459     上海市瑞林路800弄
4525         上海市立新村
4585     上海市瑞林路800弄
4600         上海市太平村
4664         上海市星光村
4672         上海市星火村
4676         上海市幸福村
4722         上海市红光村
4729         上海市立新村
4797      上海市鹤溪街52弄
4831         上海市金汇村
4832         上海市金家村
4882      上海市鹤溪街52弄
4931         上海市团结村
4991         上海市北新村
4996         上海市城南村
5036    上海市环城东路260弄
